In [1]:
import pandas as pd
import requests
from bs4 import BeautifulSoup
import OpenDartReader
api_key = 'f2e08d4ed3de0ba3d5cbf59c04c223e02b1751a2'
stock_code = '005930'   # 삼성전자
dart = OpenDartReader(api_key)

In [2]:
# company() : 기업의 개황정보 - corp_code 또는 stock_code로 조회
dart.company('00126380')
# dart.company('005930')

{'status': '000',
 'message': '정상',
 'corp_code': '00126380',
 'corp_name': '삼성전자(주)',
 'corp_name_eng': 'SAMSUNG ELECTRONICS CO,.LTD',
 'stock_name': '삼성전자',
 'stock_code': '005930',
 'ceo_nm': '한종희, 경계현',
 'corp_cls': 'Y',
 'jurir_no': '1301110006246',
 'bizr_no': '1248100998',
 'adres': '경기도 수원시 영통구  삼성로 129 (매탄동)',
 'hm_url': 'www.samsung.com/sec',
 'ir_url': '',
 'phn_no': '02-2255-0114',
 'fax_no': '031-200-7538',
 'induty_code': '264',
 'est_dt': '19690113',
 'acc_mt': '12'}

In [10]:
xml_text = dart.document('20210309000744')

In [6]:
xml_text

'<?xml version="1.0" encoding="utf-8"?>\r\n\r\n\r\n<DOCUMENT xmlns:xsi="http://www.w3.org/2001/XMLSchema-instance" xsi:noNamespaceSchemaLocation="dart3.xsd">\n\n<DOCUMENT-HEADER AEXT-CLASS="Y">\n<DOCUMENT-NAME ACODE="11011">사업보고서</DOCUMENT-NAME>\n<FORMULA-VERSION ADATE="20210122">4.2</FORMULA-VERSION>\n<COMPANY-NAME AREGCIK="00126380">삼성전자</COMPANY-NAME>\n\n<SUMMARY>\n<EXTRACTION ACODE="LINK_FLAG" AFEATURE="BOTH">C</EXTRACTION>\n<EXTRACTION ACODE="FIN_TYPE" AFEATURE="BOTH">A</EXTRACTION>\n<EXTRACTION ACODE="CRP_RGS_NO_TEMP" AFEATURE="BOTH">130111-0006246</EXTRACTION>\n</SUMMARY>\n</DOCUMENT-HEADER>\n\n<BODY>\n\n<INSERTION ABASISNUMBER="SE1" AFREQUENCY="0" ADUPLICATION="N">\n<COMMENT>◆click◆ 정정문서 작성시 『정오표』 삽입</COMMENT>\n<LIBRARYLIST>정정신고(보고)-대표이사등의확인.LCommon</LIBRARYLIST>\n</INSERTION>\n\n<COVER>\n<P></P>\n<COVER-TITLE ATOC="Y" AASSOCNOTE="COVER">사 업 보 고 서</COVER-TITLE>\n<P>&cr;&cr;&cr;</P>\n<P USERMARK="F-16">                                    (제 52 기)</P>\n\n<TABLE-GROUP ACLASS="COVE

In [7]:
xml_text_list = dart.document_all('20220816001711')

In [7]:
import xmltodict
# xmltodict 모듈을 사용해서 xml 데이터를 파이썬의 OrderedDict 타입으로 변환
dict_data = xmltodict.parse(xml_text)

ExpatError: undefined entity: line 28, column 3

In [9]:
dict_data

NameError: name 'dict_data' is not defined

In [10]:
rpt = dart.sub_docs('20210309000744')

ConnectionError: ('Connection aborted.', RemoteDisconnected('Remote end closed connection without response'))

In [4]:
subreports = []
str_expr = "title.str.contains('5. 재무제표 주석')"
for i, row in report.iterrows():
    if '사업보고서' in row['report_nm']:
        num = row['rcept_no']
        rpt = dart.sub_docs(num)
        rpt_data = rpt.query(str_expr)       # data frame
        rpt_title = rpt_data.iloc[0]['title']
        rpt_url = rpt_data.iloc[0]['url']
        subreports.append({'rpt_no' : num, 'rpt_title' : rpt_title, 'rpt_url' : rpt_url})

ConnectionError: ('Connection aborted.', RemoteDisconnected('Remote end closed connection without response'))

In [18]:
for r in subreports:
    print(r['rpt_no'])
    print(r['rpt_title'])
    print(r['rpt_url'])

20210309000744
5. 재무제표 주석
http://dart.fss.or.kr/report/viewer.do?rcpNo=20210309000744&dcmNo=7861003&eleId=17&offset=1444226&length=476709&dtd=dart3.xsd


In [19]:
def str2num(x):
    if "," in x:
        x = x.replace(",","")
    if x.startswith("(") and x.endswith(")"):
        x = x.lstrip("(")
        x = x.rstrip(")")
        float_num = float(x) * (-1)
    else:
        x = x.lstrip("(")
        x = x.rstrip(")")     
        float_num = float(x)
    return float_num

In [20]:
for r in subreports:
    url = r['rpt_url']
    response = requests.get(url)
    if response.status_code == 200:     # URL GET '200 정상'
        soup = BeautifulSoup(response.text)
        # CSS Selector를 이용하여 가져오기
        # table:nth-child(370) => 매 데이터마다 370 숫자가 일정하지 않다.
        # 기금이 적립된 확정급여부채의 현재가치
        value1 = soup.select_one("body > table:nth-child(370) > tbody > tr:nth-child(1) > td:nth-child(2)")
        # 사외적립자산의 공정가치
        value2 = soup.select_one("body > table:nth-child(370) > tbody > tr:nth-child(4) > td:nth-child(2)")
        if value1 is not None:
            print("확정급여부채: ", str2num(value1.string))
        if value2 is not None:
            print("사외적립자산: ", str2num(value2.string))
    else:
        print("URL GET Error")

확정급여부채:  9740095.0
사외적립자산:  -10916538.0


In [21]:
for r in subreports:
    url = r['rpt_url']
    df_data = pd.read_html(url)
    for df in df_data:
        if df.columns[0] == '구 분':
            row = df.shape[0]
            for i in range(0, row):
                if df.iloc[i,0] == '기금이 적립된 확정급여채무의 현재가치':
                    print("확정급여부채: ", str2num(df.iloc[i,1]))
                if df.iloc[i,0] == '사외적립자산의 공정가치':
                    print("사외적립자산: ", str2num(df.iloc[i,1]))    

확정급여부채:  9740095.0
사외적립자산:  -10916538.0
